## Load libraries

In [18]:
import numpy as np
import pandas as pd
import re
from scipy import stats
from scipy.stats import boxcox
from scipy.special import inv_boxcox
import math
import matplotlib.pyplot as plt
from sklearn.linear_model import LinearRegression, ElasticNet, Ridge, Lasso, BayesianRidge, LassoLarsIC
from sklearn.ensemble import RandomForestRegressor as rfr,  GradientBoostingRegressor
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import RobustScaler
from sklearn.base import BaseEstimator, TransformerMixin, RegressorMixin, clone
from sklearn.model_selection import KFold, cross_val_score, train_test_split
from sklearn.metrics import mean_squared_error, SCORERS
from sklearn.model_selection import GridSearchCV

import lightgbm as lgb
import xgboost as xgb
from catboost import CatBoostRegressor
from mlxtend.regressor import StackingRegressor, StackingCVRegressor

%matplotlib inline
plt.style.use('ggplot')
from IPython.display import display
display.max_columns = None
display.max_rows = None

## Load Data

In [2]:
train = pd.read_csv('../data/train_processed_ord.csv')
test_raw = pd.read_csv('../data/test.csv')
train_raw=pd.read_csv('../data/train.csv')
test = pd.read_csv('../data/test_processed_ord.csv')
yt, lmda = stats.boxcox(train['SalePrice']) # Boxcox of SalePrice
act_pred = train['SalePrice']
X = train.drop(columns='SalePrice')
X = X.loc[:, X.columns!='HouseStyle_2.5Fin'] #HouseStyle_2.5Fin in training.csv but not in test.csv

## Skewness (adjust Skewness of numeric columns)
 - Adjust features with skewness greater than 0.75

In [3]:
numeric=X.loc[:, X.columns != 'IsPool']
numeric = numeric.loc[:, numeric.columns !='IsGarage']
numerical = numeric.dtypes[:27].index.to_list()
skewed = X[numerical].apply(lambda x: x.skew()).sort_values()
skewdf = pd.DataFrame({'Skew': skewed})
skewdf = skewdf[(skewdf)>0.75]
from scipy.special import boxcox1p
skewed = skewdf.index
lam = 0.15
for feat in skewed:
    X[feat] = boxcox1p(X[feat], lam)
    test[feat] = boxcox1p(test[feat], lam)
# newskewed = X[numerical].apply(lambda x: x.skew()).sort_values()

## Evaluate Models

In [4]:
def rmse(model, X=X, yt=yt, lmda=lmda):
    y=train['SalePrice']
    kfold = KFold(n_splits=5, shuffle=True, random_state=1)
    RMSE_list=[]
    for train_id, holdout_id in kfold.split(X, yt):
        instance = clone(model)
        instance.fit(X.iloc[train_id], yt[train_id])
        y_pred = instance.predict(X.iloc[holdout_id])
        y_pred = ((y_pred*lmda)+1)**(1/lmda)
        y_mean=np.mean(y[holdout_id])
        RSE=np.sum((np.log(y_pred)-np.log(y[holdout_id]))**2)
        MSE=RSE/len(holdout_id)
        RMSE=np.sqrt(MSE)
        RMSE_list.append(RMSE)
    return RMSE_list

## Train Test Split

In [5]:
print(X.shape)
print(test.shape)

(1454, 177)
(1459, 177)


In [6]:
X_tr, X_val, y_tr, y_val = train_test_split(X, yt, test_size=0.2, random_state=1)

# Level I Models:

In [7]:
ridge = Ridge(normalize=True, alpha=0.046)
lasso = Lasso(normalize=True, alpha=3.909090909090909e-05)
net = ElasticNet(normalize=True, alpha=3.842105263157895e-05, l1_ratio=1)
catB = CatBoostRegressor(iterations=3000, random_seed=1, depth=5,
                        loss_function='RMSE')
lgb_= lgb.LGBMRegressor(objective='regression',num_leaves=8,
                              learning_rate=0.05, n_estimators=760,
                              max_bin = 55, bagging_fraction = 0.667,
                              bagging_freq = 5, feature_fraction = 0.4181818181818182,
                              feature_fraction_seed=1, bagging_seed=1,
                              min_data_in_leaf =6, min_sum_hessian_in_leaf = 5)
gb = GradientBoostingRegressor(n_estimators=3000,
                               learning_rate=0.05,
                               max_depth=2,
                               max_features='sqrt',
                               min_samples_leaf=3,
                               min_samples_split=14, 
                               loss='huber', 
                               random_state =5)

# Level II Models

## Level II : 1. Simple Averaging Model

In [26]:
class AveragingModels(BaseEstimator, RegressorMixin, TransformerMixin):
    def __init__(self, models):
        self.models = models
        
    # we define clones of the original models to fit the data in
    def fit(self, X, y):
        self.models_ = [clone(x) for x in self.models]
        
        # Train cloned base models
        for model in self.models_:
            model.fit(X, y)

        return self
    
    #Now we do the predictions for cloned models and average them
    def predict(self, X):
        predictions = np.column_stack([
            model.predict(X) for model in self.models_
        ])
        return np.mean(predictions, axis=1)   


In [27]:
simple_stack_model = AveragingModels(models = (lasso, net, catB, gb))
np.mean(rmse(simple_stack_model))
# simple average 1: ridge, lasso, net, catB, lgb_  ****rmse: 0.1092269247789186
# simple average 2: ridge, lasso, net, catB        ****rmse: 0.11026486262230677
# simple average 3: lasso, net, catB, lgb_         ****rmse: 0.10921533915676931
# simple average 4: lasso, net, catB, gb           ****rmse: 0.10871493509743232


Learning rate set to 0.017396
0:	learn: 0.1505543	total: 3.59ms	remaining: 10.8s
1:	learn: 0.1487864	total: 6.67ms	remaining: 10s
2:	learn: 0.1471340	total: 9.92ms	remaining: 9.91s
3:	learn: 0.1454217	total: 12.9ms	remaining: 9.68s
4:	learn: 0.1438943	total: 15.7ms	remaining: 9.39s
5:	learn: 0.1422813	total: 18.9ms	remaining: 9.45s
6:	learn: 0.1408089	total: 22ms	remaining: 9.38s
7:	learn: 0.1392242	total: 24.7ms	remaining: 9.24s
8:	learn: 0.1377242	total: 27.6ms	remaining: 9.16s
9:	learn: 0.1363748	total: 30.4ms	remaining: 9.09s
10:	learn: 0.1348971	total: 33.2ms	remaining: 9.03s
11:	learn: 0.1334662	total: 36.4ms	remaining: 9.05s
12:	learn: 0.1322014	total: 39.5ms	remaining: 9.07s
13:	learn: 0.1307917	total: 42.3ms	remaining: 9.03s
14:	learn: 0.1294696	total: 45.3ms	remaining: 9.02s
15:	learn: 0.1280315	total: 48.5ms	remaining: 9.04s
16:	learn: 0.1267869	total: 51.5ms	remaining: 9.04s
17:	learn: 0.1254464	total: 54.4ms	remaining: 9.01s
18:	learn: 0.1241810	total: 57.5ms	remaining: 9.

195:	learn: 0.0486267	total: 566ms	remaining: 8.09s
196:	learn: 0.0485278	total: 570ms	remaining: 8.1s
197:	learn: 0.0484424	total: 573ms	remaining: 8.1s
198:	learn: 0.0483428	total: 575ms	remaining: 8.1s
199:	learn: 0.0482388	total: 579ms	remaining: 8.11s
200:	learn: 0.0481500	total: 582ms	remaining: 8.11s
201:	learn: 0.0480499	total: 585ms	remaining: 8.1s
202:	learn: 0.0479454	total: 587ms	remaining: 8.09s
203:	learn: 0.0478439	total: 590ms	remaining: 8.09s
204:	learn: 0.0477612	total: 593ms	remaining: 8.08s
205:	learn: 0.0476700	total: 596ms	remaining: 8.09s
206:	learn: 0.0475825	total: 599ms	remaining: 8.08s
207:	learn: 0.0474842	total: 601ms	remaining: 8.07s
208:	learn: 0.0474105	total: 603ms	remaining: 8.06s
209:	learn: 0.0473158	total: 605ms	remaining: 8.04s
210:	learn: 0.0472594	total: 607ms	remaining: 8.03s
211:	learn: 0.0471661	total: 609ms	remaining: 8.01s
212:	learn: 0.0470875	total: 611ms	remaining: 7.99s
213:	learn: 0.0469944	total: 612ms	remaining: 7.97s
214:	learn: 0.04

405:	learn: 0.0380156	total: 940ms	remaining: 6.01s
406:	learn: 0.0379924	total: 942ms	remaining: 6s
407:	learn: 0.0379690	total: 944ms	remaining: 6s
408:	learn: 0.0379368	total: 945ms	remaining: 5.99s
409:	learn: 0.0379077	total: 948ms	remaining: 5.99s
410:	learn: 0.0378863	total: 951ms	remaining: 5.99s
411:	learn: 0.0378703	total: 954ms	remaining: 5.99s
412:	learn: 0.0378407	total: 957ms	remaining: 5.99s
413:	learn: 0.0378178	total: 960ms	remaining: 6s
414:	learn: 0.0377897	total: 964ms	remaining: 6s
415:	learn: 0.0377519	total: 967ms	remaining: 6.01s
416:	learn: 0.0377367	total: 970ms	remaining: 6.01s
417:	learn: 0.0377076	total: 972ms	remaining: 6.01s
418:	learn: 0.0376715	total: 975ms	remaining: 6s
419:	learn: 0.0376450	total: 976ms	remaining: 6s
420:	learn: 0.0376106	total: 978ms	remaining: 5.99s
421:	learn: 0.0375820	total: 979ms	remaining: 5.98s
422:	learn: 0.0375609	total: 981ms	remaining: 5.98s
423:	learn: 0.0375309	total: 982ms	remaining: 5.97s
424:	learn: 0.0375007	total: 9

635:	learn: 0.0332080	total: 1.31s	remaining: 4.87s
636:	learn: 0.0331882	total: 1.31s	remaining: 4.87s
637:	learn: 0.0331653	total: 1.32s	remaining: 4.87s
638:	learn: 0.0331518	total: 1.32s	remaining: 4.87s
639:	learn: 0.0331407	total: 1.32s	remaining: 4.88s
640:	learn: 0.0331291	total: 1.33s	remaining: 4.88s
641:	learn: 0.0331112	total: 1.33s	remaining: 4.88s
642:	learn: 0.0330885	total: 1.33s	remaining: 4.88s
643:	learn: 0.0330771	total: 1.33s	remaining: 4.88s
644:	learn: 0.0330604	total: 1.33s	remaining: 4.88s
645:	learn: 0.0330365	total: 1.34s	remaining: 4.87s
646:	learn: 0.0330252	total: 1.34s	remaining: 4.87s
647:	learn: 0.0330062	total: 1.34s	remaining: 4.87s
648:	learn: 0.0329887	total: 1.34s	remaining: 4.87s
649:	learn: 0.0329612	total: 1.34s	remaining: 4.86s
650:	learn: 0.0329590	total: 1.35s	remaining: 4.86s
651:	learn: 0.0329335	total: 1.35s	remaining: 4.85s
652:	learn: 0.0329194	total: 1.35s	remaining: 4.85s
653:	learn: 0.0329173	total: 1.35s	remaining: 4.84s
654:	learn: 

855:	learn: 0.0297253	total: 1.68s	remaining: 4.22s
856:	learn: 0.0297077	total: 1.69s	remaining: 4.21s
857:	learn: 0.0296945	total: 1.69s	remaining: 4.22s
858:	learn: 0.0296787	total: 1.69s	remaining: 4.21s
859:	learn: 0.0296581	total: 1.69s	remaining: 4.21s
860:	learn: 0.0296424	total: 1.7s	remaining: 4.21s
861:	learn: 0.0296229	total: 1.7s	remaining: 4.21s
862:	learn: 0.0296049	total: 1.7s	remaining: 4.21s
863:	learn: 0.0295895	total: 1.7s	remaining: 4.21s
864:	learn: 0.0295772	total: 1.71s	remaining: 4.21s
865:	learn: 0.0295543	total: 1.71s	remaining: 4.21s
866:	learn: 0.0295440	total: 1.71s	remaining: 4.21s
867:	learn: 0.0295280	total: 1.71s	remaining: 4.21s
868:	learn: 0.0295079	total: 1.71s	remaining: 4.2s
869:	learn: 0.0294982	total: 1.72s	remaining: 4.2s
870:	learn: 0.0294811	total: 1.72s	remaining: 4.2s
871:	learn: 0.0294665	total: 1.72s	remaining: 4.19s
872:	learn: 0.0294597	total: 1.72s	remaining: 4.19s
873:	learn: 0.0294498	total: 1.72s	remaining: 4.19s
874:	learn: 0.02943

...

2421:	learn: 0.0162587	total: 4.27s	remaining: 1.02s
2422:	learn: 0.0162504	total: 4.27s	remaining: 1.02s
2423:	learn: 0.0162445	total: 4.27s	remaining: 1.01s
2424:	learn: 0.0162389	total: 4.28s	remaining: 1.01s
2425:	learn: 0.0162324	total: 4.28s	remaining: 1.01s
2426:	learn: 0.0162283	total: 4.28s	remaining: 1.01s
2427:	learn: 0.0162232	total: 4.29s	remaining: 1.01s
2428:	learn: 0.0162217	total: 4.29s	remaining: 1.01s
2429:	learn: 0.0162152	total: 4.29s	remaining: 1.01s
2430:	learn: 0.0162092	total: 4.29s	remaining: 1s
2431:	learn: 0.0162049	total: 4.3s	remaining: 1s
2432:	learn: 0.0162003	total: 4.3s	remaining: 1s
2433:	learn: 0.0161919	total: 4.3s	remaining: 1s
2434:	learn: 0.0161858	total: 4.3s	remaining: 999ms
2435:	learn: 0.0161780	total: 4.3s	remaining: 997ms
2436:	learn: 0.0161727	total: 4.31s	remaining: 995ms
2437:	learn: 0.0161677	total: 4.31s	remaining: 993ms
2438:	learn: 0.0161586	total: 4.31s	remaining: 992ms
2439:	learn: 0.0161507	total: 4.31s	remaining: 990ms
2440:	lear

2611:	learn: 0.0152766	total: 4.64s	remaining: 689ms
2612:	learn: 0.0152690	total: 4.64s	remaining: 688ms
2613:	learn: 0.0152618	total: 4.65s	remaining: 686ms
2614:	learn: 0.0152559	total: 4.65s	remaining: 685ms
2615:	learn: 0.0152526	total: 4.65s	remaining: 683ms
2616:	learn: 0.0152457	total: 4.66s	remaining: 681ms
2617:	learn: 0.0152393	total: 4.66s	remaining: 680ms
2618:	learn: 0.0152342	total: 4.66s	remaining: 678ms
2619:	learn: 0.0152302	total: 4.66s	remaining: 676ms
2620:	learn: 0.0152297	total: 4.67s	remaining: 675ms
2621:	learn: 0.0152225	total: 4.67s	remaining: 673ms
2622:	learn: 0.0152161	total: 4.67s	remaining: 671ms
2623:	learn: 0.0152124	total: 4.67s	remaining: 670ms
2624:	learn: 0.0152061	total: 4.68s	remaining: 668ms
2625:	learn: 0.0152015	total: 4.68s	remaining: 667ms
2626:	learn: 0.0151975	total: 4.68s	remaining: 665ms
2627:	learn: 0.0151930	total: 4.68s	remaining: 663ms
2628:	learn: 0.0151860	total: 4.68s	remaining: 661ms
2629:	learn: 0.0151762	total: 4.69s	remaining:

2805:	learn: 0.0142831	total: 5.01s	remaining: 347ms
2806:	learn: 0.0142806	total: 5.02s	remaining: 345ms
2807:	learn: 0.0142695	total: 5.02s	remaining: 343ms
2808:	learn: 0.0142671	total: 5.02s	remaining: 341ms
2809:	learn: 0.0142607	total: 5.02s	remaining: 340ms
2810:	learn: 0.0142575	total: 5.03s	remaining: 338ms
2811:	learn: 0.0142567	total: 5.03s	remaining: 336ms
2812:	learn: 0.0142543	total: 5.03s	remaining: 335ms
2813:	learn: 0.0142500	total: 5.04s	remaining: 333ms
2814:	learn: 0.0142458	total: 5.04s	remaining: 331ms
2815:	learn: 0.0142405	total: 5.04s	remaining: 329ms
2816:	learn: 0.0142336	total: 5.04s	remaining: 328ms
2817:	learn: 0.0142297	total: 5.05s	remaining: 326ms
2818:	learn: 0.0142263	total: 5.05s	remaining: 324ms
2819:	learn: 0.0142186	total: 5.05s	remaining: 322ms
2820:	learn: 0.0142133	total: 5.05s	remaining: 321ms
2821:	learn: 0.0142075	total: 5.05s	remaining: 319ms
2822:	learn: 0.0142060	total: 5.06s	remaining: 317ms
2823:	learn: 0.0142024	total: 5.06s	remaining:

2994:	learn: 0.0134234	total: 5.39s	remaining: 8.99ms
2995:	learn: 0.0134190	total: 5.39s	remaining: 7.2ms
2996:	learn: 0.0134154	total: 5.39s	remaining: 5.4ms
2997:	learn: 0.0134122	total: 5.39s	remaining: 3.6ms
2998:	learn: 0.0134074	total: 5.4s	remaining: 1.8ms
2999:	learn: 0.0134053	total: 5.4s	remaining: 0us


0.10871493509743232

In [28]:
simple_stack_model.fit(X, yt)
prediction=simple_stack_model.predict(test)
prediction=((prediction*lmda)+1)**(1/lmda)
pred = pd.DataFrame(prediction, columns=['SalePrice'])
ID = test_raw[['Id']]
sub=pd.merge(ID, pred, left_on = ID.index, right_on = pred.index).drop(columns=['key_0'])
sub.to_csv('../Submissions/simple_average4.csv',index=False)
prediction

Learning rate set to 0.018102
0:	learn: 0.1518620	total: 3.85ms	remaining: 11.6s
1:	learn: 0.1500538	total: 7.07ms	remaining: 10.6s
2:	learn: 0.1482669	total: 10ms	remaining: 10s
3:	learn: 0.1465452	total: 12.9ms	remaining: 9.66s
4:	learn: 0.1449003	total: 15.9ms	remaining: 9.55s
5:	learn: 0.1431763	total: 18.9ms	remaining: 9.42s
6:	learn: 0.1416235	total: 22.1ms	remaining: 9.45s
7:	learn: 0.1398936	total: 25.1ms	remaining: 9.39s
8:	learn: 0.1383474	total: 28.1ms	remaining: 9.34s
9:	learn: 0.1367867	total: 31.2ms	remaining: 9.34s
10:	learn: 0.1352560	total: 34.4ms	remaining: 9.34s
11:	learn: 0.1338080	total: 37.7ms	remaining: 9.39s
12:	learn: 0.1324559	total: 40.3ms	remaining: 9.27s
13:	learn: 0.1309299	total: 43.6ms	remaining: 9.29s
14:	learn: 0.1295830	total: 46.5ms	remaining: 9.25s
15:	learn: 0.1281371	total: 49.5ms	remaining: 9.22s
16:	learn: 0.1267530	total: 52.3ms	remaining: 9.19s
17:	learn: 0.1253540	total: 55.1ms	remaining: 9.13s
18:	learn: 0.1240230	total: 58.1ms	remaining: 9.

222:	learn: 0.0472009	total: 564ms	remaining: 7.02s
223:	learn: 0.0471405	total: 567ms	remaining: 7.03s
224:	learn: 0.0470815	total: 570ms	remaining: 7.03s
225:	learn: 0.0470048	total: 573ms	remaining: 7.04s
226:	learn: 0.0469413	total: 576ms	remaining: 7.03s
227:	learn: 0.0468781	total: 578ms	remaining: 7.03s
228:	learn: 0.0468114	total: 581ms	remaining: 7.03s
229:	learn: 0.0467399	total: 584ms	remaining: 7.03s
230:	learn: 0.0466626	total: 586ms	remaining: 7.03s
231:	learn: 0.0465888	total: 589ms	remaining: 7.03s
232:	learn: 0.0465233	total: 592ms	remaining: 7.03s
233:	learn: 0.0464448	total: 594ms	remaining: 7.02s
234:	learn: 0.0463804	total: 597ms	remaining: 7.03s
235:	learn: 0.0463337	total: 599ms	remaining: 7.02s
236:	learn: 0.0462654	total: 601ms	remaining: 7.01s
237:	learn: 0.0461950	total: 603ms	remaining: 6.99s
238:	learn: 0.0461439	total: 604ms	remaining: 6.98s
239:	learn: 0.0460823	total: 606ms	remaining: 6.96s
240:	learn: 0.0460021	total: 607ms	remaining: 6.95s
241:	learn: 

429:	learn: 0.0390486	total: 935ms	remaining: 5.59s
430:	learn: 0.0390290	total: 938ms	remaining: 5.59s
431:	learn: 0.0390057	total: 940ms	remaining: 5.59s
432:	learn: 0.0389897	total: 941ms	remaining: 5.58s
433:	learn: 0.0389736	total: 943ms	remaining: 5.57s
434:	learn: 0.0389350	total: 945ms	remaining: 5.57s
435:	learn: 0.0389094	total: 946ms	remaining: 5.56s
436:	learn: 0.0388915	total: 948ms	remaining: 5.56s
437:	learn: 0.0388628	total: 949ms	remaining: 5.55s
438:	learn: 0.0388437	total: 950ms	remaining: 5.54s
439:	learn: 0.0388124	total: 953ms	remaining: 5.54s
440:	learn: 0.0387876	total: 956ms	remaining: 5.54s
441:	learn: 0.0387629	total: 958ms	remaining: 5.54s
442:	learn: 0.0387433	total: 961ms	remaining: 5.55s
443:	learn: 0.0387222	total: 964ms	remaining: 5.55s
444:	learn: 0.0386999	total: 966ms	remaining: 5.55s
445:	learn: 0.0386747	total: 969ms	remaining: 5.55s
446:	learn: 0.0386495	total: 971ms	remaining: 5.55s
447:	learn: 0.0386296	total: 974ms	remaining: 5.55s
448:	learn: 

643:	learn: 0.0348619	total: 1.31s	remaining: 4.8s
644:	learn: 0.0348440	total: 1.31s	remaining: 4.79s
645:	learn: 0.0348300	total: 1.31s	remaining: 4.79s
646:	learn: 0.0348108	total: 1.32s	remaining: 4.79s
647:	learn: 0.0347874	total: 1.32s	remaining: 4.78s
648:	learn: 0.0347768	total: 1.32s	remaining: 4.78s
649:	learn: 0.0347618	total: 1.32s	remaining: 4.78s
650:	learn: 0.0347459	total: 1.32s	remaining: 4.77s
651:	learn: 0.0347228	total: 1.33s	remaining: 4.78s
652:	learn: 0.0347048	total: 1.33s	remaining: 4.78s
653:	learn: 0.0346822	total: 1.33s	remaining: 4.77s
654:	learn: 0.0346731	total: 1.33s	remaining: 4.78s
655:	learn: 0.0346579	total: 1.34s	remaining: 4.77s
656:	learn: 0.0346443	total: 1.34s	remaining: 4.77s
657:	learn: 0.0346388	total: 1.34s	remaining: 4.77s
658:	learn: 0.0346228	total: 1.34s	remaining: 4.77s
659:	learn: 0.0346133	total: 1.35s	remaining: 4.77s
660:	learn: 0.0345922	total: 1.35s	remaining: 4.77s
661:	learn: 0.0345699	total: 1.35s	remaining: 4.77s
662:	learn: 0

870:	learn: 0.0317468	total: 1.68s	remaining: 4.11s
871:	learn: 0.0317341	total: 1.69s	remaining: 4.11s
872:	learn: 0.0317171	total: 1.69s	remaining: 4.11s
873:	learn: 0.0317063	total: 1.69s	remaining: 4.11s
874:	learn: 0.0316925	total: 1.69s	remaining: 4.11s
875:	learn: 0.0316753	total: 1.7s	remaining: 4.11s
876:	learn: 0.0316548	total: 1.7s	remaining: 4.11s
877:	learn: 0.0316395	total: 1.7s	remaining: 4.11s
878:	learn: 0.0316217	total: 1.7s	remaining: 4.11s
879:	learn: 0.0316107	total: 1.71s	remaining: 4.11s
880:	learn: 0.0315958	total: 1.71s	remaining: 4.11s
881:	learn: 0.0315886	total: 1.71s	remaining: 4.11s
882:	learn: 0.0315710	total: 1.71s	remaining: 4.11s
883:	learn: 0.0315582	total: 1.71s	remaining: 4.1s
884:	learn: 0.0315455	total: 1.72s	remaining: 4.1s
885:	learn: 0.0315327	total: 1.72s	remaining: 4.1s
886:	learn: 0.0315280	total: 1.72s	remaining: 4.09s
887:	learn: 0.0315087	total: 1.72s	remaining: 4.09s
888:	learn: 0.0314980	total: 1.72s	remaining: 4.09s
889:	learn: 0.03148

...

2274:	learn: 0.0192162	total: 3.92s	remaining: 1.25s
2275:	learn: 0.0192122	total: 3.92s	remaining: 1.25s
2276:	learn: 0.0192112	total: 3.92s	remaining: 1.25s
2277:	learn: 0.0192018	total: 3.92s	remaining: 1.24s
2278:	learn: 0.0191938	total: 3.93s	remaining: 1.24s
2279:	learn: 0.0191899	total: 3.93s	remaining: 1.24s
2280:	learn: 0.0191810	total: 3.93s	remaining: 1.24s
2281:	learn: 0.0191730	total: 3.93s	remaining: 1.24s
2282:	learn: 0.0191676	total: 3.94s	remaining: 1.24s
2283:	learn: 0.0191615	total: 3.94s	remaining: 1.23s
2284:	learn: 0.0191591	total: 3.94s	remaining: 1.23s
2285:	learn: 0.0191567	total: 3.94s	remaining: 1.23s
2286:	learn: 0.0191549	total: 3.94s	remaining: 1.23s
2287:	learn: 0.0191543	total: 3.95s	remaining: 1.23s
2288:	learn: 0.0191467	total: 3.95s	remaining: 1.23s
2289:	learn: 0.0191435	total: 3.95s	remaining: 1.22s
2290:	learn: 0.0191351	total: 3.95s	remaining: 1.22s
2291:	learn: 0.0191272	total: 3.95s	remaining: 1.22s
2292:	learn: 0.0191212	total: 3.95s	remaining:

2507:	learn: 0.0179222	total: 4.29s	remaining: 841ms
2508:	learn: 0.0179149	total: 4.29s	remaining: 840ms
2509:	learn: 0.0179063	total: 4.29s	remaining: 838ms
2510:	learn: 0.0179044	total: 4.3s	remaining: 837ms
2511:	learn: 0.0179041	total: 4.3s	remaining: 835ms
2512:	learn: 0.0179013	total: 4.3s	remaining: 834ms
2513:	learn: 0.0178981	total: 4.3s	remaining: 832ms
2514:	learn: 0.0178953	total: 4.31s	remaining: 831ms
2515:	learn: 0.0178908	total: 4.31s	remaining: 829ms
2516:	learn: 0.0178877	total: 4.31s	remaining: 828ms
2517:	learn: 0.0178845	total: 4.31s	remaining: 826ms
2518:	learn: 0.0178804	total: 4.32s	remaining: 824ms
2519:	learn: 0.0178727	total: 4.32s	remaining: 823ms
2520:	learn: 0.0178685	total: 4.32s	remaining: 821ms
2521:	learn: 0.0178620	total: 4.32s	remaining: 819ms
2522:	learn: 0.0178585	total: 4.32s	remaining: 817ms
2523:	learn: 0.0178534	total: 4.32s	remaining: 816ms
2524:	learn: 0.0178465	total: 4.33s	remaining: 814ms
2525:	learn: 0.0178401	total: 4.33s	remaining: 812

2740:	learn: 0.0168255	total: 4.66s	remaining: 440ms
2741:	learn: 0.0168228	total: 4.66s	remaining: 439ms
2742:	learn: 0.0168154	total: 4.67s	remaining: 437ms
2743:	learn: 0.0168101	total: 4.67s	remaining: 436ms
2744:	learn: 0.0168046	total: 4.67s	remaining: 434ms
2745:	learn: 0.0168016	total: 4.67s	remaining: 432ms
2746:	learn: 0.0168012	total: 4.67s	remaining: 431ms
2747:	learn: 0.0167955	total: 4.68s	remaining: 429ms
2748:	learn: 0.0167895	total: 4.68s	remaining: 427ms
2749:	learn: 0.0167812	total: 4.68s	remaining: 426ms
2750:	learn: 0.0167772	total: 4.68s	remaining: 424ms
2751:	learn: 0.0167705	total: 4.69s	remaining: 422ms
2752:	learn: 0.0167647	total: 4.69s	remaining: 421ms
2753:	learn: 0.0167589	total: 4.69s	remaining: 419ms
2754:	learn: 0.0167539	total: 4.69s	remaining: 417ms
2755:	learn: 0.0167482	total: 4.69s	remaining: 416ms
2756:	learn: 0.0167449	total: 4.7s	remaining: 414ms
2757:	learn: 0.0167400	total: 4.7s	remaining: 412ms
2758:	learn: 0.0167340	total: 4.7s	remaining: 41

2976:	learn: 0.0157538	total: 5.03s	remaining: 38.9ms
2977:	learn: 0.0157493	total: 5.04s	remaining: 37.2ms
2978:	learn: 0.0157471	total: 5.04s	remaining: 35.5ms
2979:	learn: 0.0157441	total: 5.04s	remaining: 33.8ms
2980:	learn: 0.0157396	total: 5.04s	remaining: 32.1ms
2981:	learn: 0.0157355	total: 5.05s	remaining: 30.5ms
2982:	learn: 0.0157314	total: 5.05s	remaining: 28.8ms
2983:	learn: 0.0157276	total: 5.05s	remaining: 27.1ms
2984:	learn: 0.0157207	total: 5.05s	remaining: 25.4ms
2985:	learn: 0.0157142	total: 5.06s	remaining: 23.7ms
2986:	learn: 0.0157107	total: 5.06s	remaining: 22ms
2987:	learn: 0.0157027	total: 5.06s	remaining: 20.3ms
2988:	learn: 0.0157005	total: 5.06s	remaining: 18.6ms
2989:	learn: 0.0156950	total: 5.07s	remaining: 16.9ms
2990:	learn: 0.0156904	total: 5.07s	remaining: 15.2ms
2991:	learn: 0.0156857	total: 5.07s	remaining: 13.6ms
2992:	learn: 0.0156792	total: 5.07s	remaining: 11.9ms
2993:	learn: 0.0156746	total: 5.07s	remaining: 10.2ms
2994:	learn: 0.0156728	total: 

array([122571.75611929, 159669.57716928, 182424.43345927, ...,
       168013.86071821, 120336.08333047, 218332.57573737])

## Level II: 2. StackedRegressor

- Stack Model 1: ridge, lasso, net, catB, lgb_  -------- 0.10949901535498763
- Stack Model 2: ridge, lasso, net, catB, gb, lgb_  ---- 0.10895692385200376 --- best result on Kaggle.
- Stack Model 3: lasso, net, catB, gb, lgb_  ---- 0.10894088060922091
- Stack Model 4: lasso, net, catB, gb ---- 0.10892961067119138

In [29]:
stack2 = StackingCVRegressor(regressors=(ridge, lasso, net, catB, gb, lgb_),
                            meta_regressor=lasso,
                            random_state=1)
print(f"stack2 has cross validation rmse score: {np.mean(rmse(stack2))}")

Learning rate set to 0.016718
0:	learn: 0.1533077	total: 6.23ms	remaining: 18.7s
1:	learn: 0.1516920	total: 10.4ms	remaining: 15.7s
2:	learn: 0.1501157	total: 14.5ms	remaining: 14.5s
3:	learn: 0.1485219	total: 17.3ms	remaining: 13s
4:	learn: 0.1471171	total: 19.8ms	remaining: 11.9s
5:	learn: 0.1454187	total: 22.8ms	remaining: 11.4s
6:	learn: 0.1438280	total: 27.5ms	remaining: 11.8s
7:	learn: 0.1423014	total: 30.5ms	remaining: 11.4s
8:	learn: 0.1407279	total: 32.9ms	remaining: 10.9s
9:	learn: 0.1392669	total: 36.8ms	remaining: 11s
10:	learn: 0.1378578	total: 39.6ms	remaining: 10.7s
11:	learn: 0.1364693	total: 42.1ms	remaining: 10.5s
12:	learn: 0.1351016	total: 44.2ms	remaining: 10.2s
13:	learn: 0.1338031	total: 46.4ms	remaining: 9.89s
14:	learn: 0.1324164	total: 48.4ms	remaining: 9.63s
15:	learn: 0.1312482	total: 50.4ms	remaining: 9.41s
16:	learn: 0.1299093	total: 52.2ms	remaining: 9.16s
17:	learn: 0.1286409	total: 53.9ms	remaining: 8.93s
18:	learn: 0.1273882	total: 55.7ms	remaining: 8.

206:	learn: 0.0487833	total: 370ms	remaining: 5s
207:	learn: 0.0486670	total: 372ms	remaining: 5s
208:	learn: 0.0485599	total: 374ms	remaining: 5s
209:	learn: 0.0484619	total: 376ms	remaining: 5s
210:	learn: 0.0483928	total: 378ms	remaining: 5s
211:	learn: 0.0482845	total: 380ms	remaining: 5s
212:	learn: 0.0482001	total: 382ms	remaining: 5s
213:	learn: 0.0480950	total: 384ms	remaining: 5s
214:	learn: 0.0479983	total: 386ms	remaining: 4.99s
215:	learn: 0.0478998	total: 387ms	remaining: 4.99s
216:	learn: 0.0478120	total: 389ms	remaining: 4.99s
217:	learn: 0.0477085	total: 391ms	remaining: 4.99s
218:	learn: 0.0476217	total: 393ms	remaining: 4.99s
219:	learn: 0.0475239	total: 395ms	remaining: 4.99s
220:	learn: 0.0474218	total: 397ms	remaining: 4.99s
221:	learn: 0.0473200	total: 398ms	remaining: 4.98s
222:	learn: 0.0472447	total: 400ms	remaining: 4.98s
223:	learn: 0.0471597	total: 402ms	remaining: 4.98s
224:	learn: 0.0470652	total: 404ms	remaining: 4.98s
225:	learn: 0.0469991	total: 406ms	r

424:	learn: 0.0373976	total: 742ms	remaining: 4.5s
425:	learn: 0.0373688	total: 744ms	remaining: 4.5s
426:	learn: 0.0373443	total: 746ms	remaining: 4.49s
427:	learn: 0.0373111	total: 748ms	remaining: 4.49s
428:	learn: 0.0372721	total: 750ms	remaining: 4.49s
429:	learn: 0.0372286	total: 752ms	remaining: 4.49s
430:	learn: 0.0372017	total: 753ms	remaining: 4.49s
431:	learn: 0.0371713	total: 755ms	remaining: 4.49s
432:	learn: 0.0371442	total: 757ms	remaining: 4.49s
433:	learn: 0.0371173	total: 759ms	remaining: 4.49s
434:	learn: 0.0370891	total: 761ms	remaining: 4.49s
435:	learn: 0.0370708	total: 763ms	remaining: 4.48s
436:	learn: 0.0370154	total: 764ms	remaining: 4.48s
437:	learn: 0.0369896	total: 766ms	remaining: 4.48s
438:	learn: 0.0369592	total: 768ms	remaining: 4.48s
439:	learn: 0.0369227	total: 771ms	remaining: 4.48s
440:	learn: 0.0368971	total: 772ms	remaining: 4.48s
441:	learn: 0.0368592	total: 774ms	remaining: 4.48s
442:	learn: 0.0368258	total: 775ms	remaining: 4.47s
443:	learn: 0.

671:	learn: 0.0316251	total: 1.11s	remaining: 3.87s
672:	learn: 0.0316021	total: 1.12s	remaining: 3.87s
673:	learn: 0.0315952	total: 1.12s	remaining: 3.86s
674:	learn: 0.0315902	total: 1.12s	remaining: 3.86s
675:	learn: 0.0315656	total: 1.12s	remaining: 3.86s
676:	learn: 0.0315577	total: 1.13s	remaining: 3.86s
677:	learn: 0.0315448	total: 1.13s	remaining: 3.86s
678:	learn: 0.0315356	total: 1.13s	remaining: 3.86s
679:	learn: 0.0315292	total: 1.14s	remaining: 3.87s
680:	learn: 0.0315223	total: 1.14s	remaining: 3.87s
681:	learn: 0.0315007	total: 1.14s	remaining: 3.87s
682:	learn: 0.0314888	total: 1.14s	remaining: 3.87s
683:	learn: 0.0314713	total: 1.14s	remaining: 3.87s
684:	learn: 0.0314519	total: 1.14s	remaining: 3.87s
685:	learn: 0.0314459	total: 1.15s	remaining: 3.87s
686:	learn: 0.0314395	total: 1.15s	remaining: 3.87s
687:	learn: 0.0314322	total: 1.15s	remaining: 3.86s
688:	learn: 0.0314110	total: 1.15s	remaining: 3.86s
689:	learn: 0.0313841	total: 1.15s	remaining: 3.86s
690:	learn: 

923:	learn: 0.0275577	total: 1.49s	remaining: 3.35s
924:	learn: 0.0275477	total: 1.49s	remaining: 3.35s
925:	learn: 0.0275308	total: 1.5s	remaining: 3.35s
926:	learn: 0.0275178	total: 1.5s	remaining: 3.35s
927:	learn: 0.0275159	total: 1.5s	remaining: 3.35s
928:	learn: 0.0275027	total: 1.5s	remaining: 3.35s
929:	learn: 0.0274880	total: 1.5s	remaining: 3.35s
930:	learn: 0.0274748	total: 1.5s	remaining: 3.34s
931:	learn: 0.0274579	total: 1.51s	remaining: 3.34s
932:	learn: 0.0274424	total: 1.51s	remaining: 3.34s
933:	learn: 0.0274291	total: 1.51s	remaining: 3.34s
934:	learn: 0.0274268	total: 1.51s	remaining: 3.34s
935:	learn: 0.0274097	total: 1.51s	remaining: 3.34s
936:	learn: 0.0273889	total: 1.52s	remaining: 3.34s
937:	learn: 0.0273677	total: 1.52s	remaining: 3.34s
938:	learn: 0.0273579	total: 1.52s	remaining: 3.34s
939:	learn: 0.0273450	total: 1.52s	remaining: 3.33s
940:	learn: 0.0273322	total: 1.52s	remaining: 3.33s
941:	learn: 0.0273139	total: 1.52s	remaining: 3.33s
942:	learn: 0.0272

...

2150:	learn: 0.0178556	total: 4.3s	remaining: 1.7s
2151:	learn: 0.0178474	total: 4.3s	remaining: 1.69s
2152:	learn: 0.0178376	total: 4.3s	remaining: 1.69s
2153:	learn: 0.0178333	total: 4.3s	remaining: 1.69s
2154:	learn: 0.0178273	total: 4.31s	remaining: 1.69s
2155:	learn: 0.0178242	total: 4.31s	remaining: 1.69s
2156:	learn: 0.0178162	total: 4.31s	remaining: 1.69s
2157:	learn: 0.0178125	total: 4.32s	remaining: 1.68s
2158:	learn: 0.0178093	total: 4.32s	remaining: 1.68s
2159:	learn: 0.0177997	total: 4.32s	remaining: 1.68s
2160:	learn: 0.0177917	total: 4.32s	remaining: 1.68s
2161:	learn: 0.0177841	total: 4.33s	remaining: 1.68s
2162:	learn: 0.0177830	total: 4.33s	remaining: 1.68s
2163:	learn: 0.0177735	total: 4.33s	remaining: 1.67s
2164:	learn: 0.0177642	total: 4.33s	remaining: 1.67s
2165:	learn: 0.0177586	total: 4.34s	remaining: 1.67s
2166:	learn: 0.0177498	total: 4.34s	remaining: 1.67s
2167:	learn: 0.0177466	total: 4.34s	remaining: 1.67s
2168:	learn: 0.0177354	total: 4.35s	remaining: 1.67

2316:	learn: 0.0168605	total: 4.67s	remaining: 1.38s
2317:	learn: 0.0168544	total: 4.68s	remaining: 1.38s
2318:	learn: 0.0168466	total: 4.68s	remaining: 1.37s
2319:	learn: 0.0168416	total: 4.68s	remaining: 1.37s
2320:	learn: 0.0168323	total: 4.69s	remaining: 1.37s
2321:	learn: 0.0168245	total: 4.69s	remaining: 1.37s
2322:	learn: 0.0168217	total: 4.69s	remaining: 1.37s
2323:	learn: 0.0168174	total: 4.69s	remaining: 1.36s
2324:	learn: 0.0168107	total: 4.7s	remaining: 1.36s
2325:	learn: 0.0168033	total: 4.7s	remaining: 1.36s
2326:	learn: 0.0167978	total: 4.7s	remaining: 1.36s
2327:	learn: 0.0167971	total: 4.71s	remaining: 1.36s
2328:	learn: 0.0167913	total: 4.71s	remaining: 1.36s
2329:	learn: 0.0167836	total: 4.71s	remaining: 1.35s
2330:	learn: 0.0167777	total: 4.71s	remaining: 1.35s
2331:	learn: 0.0167727	total: 4.72s	remaining: 1.35s
2332:	learn: 0.0167660	total: 4.72s	remaining: 1.35s
2333:	learn: 0.0167591	total: 4.72s	remaining: 1.35s
2334:	learn: 0.0167506	total: 4.72s	remaining: 1.

2506:	learn: 0.0158114	total: 5.05s	remaining: 993ms
2507:	learn: 0.0158044	total: 5.05s	remaining: 991ms
2508:	learn: 0.0157995	total: 5.05s	remaining: 989ms
2509:	learn: 0.0157939	total: 5.05s	remaining: 987ms
2510:	learn: 0.0157895	total: 5.06s	remaining: 985ms
2511:	learn: 0.0157845	total: 5.06s	remaining: 983ms
2512:	learn: 0.0157779	total: 5.06s	remaining: 981ms
2513:	learn: 0.0157745	total: 5.07s	remaining: 979ms
2514:	learn: 0.0157721	total: 5.07s	remaining: 978ms
2515:	learn: 0.0157693	total: 5.07s	remaining: 976ms
2516:	learn: 0.0157641	total: 5.08s	remaining: 974ms
2517:	learn: 0.0157562	total: 5.08s	remaining: 972ms
2518:	learn: 0.0157557	total: 5.08s	remaining: 970ms
2519:	learn: 0.0157512	total: 5.08s	remaining: 968ms
2520:	learn: 0.0157441	total: 5.09s	remaining: 966ms
2521:	learn: 0.0157398	total: 5.09s	remaining: 965ms
2522:	learn: 0.0157389	total: 5.09s	remaining: 963ms
2523:	learn: 0.0157344	total: 5.1s	remaining: 961ms
2524:	learn: 0.0157338	total: 5.1s	remaining: 9

2666:	learn: 0.0149881	total: 5.42s	remaining: 677ms
2667:	learn: 0.0149845	total: 5.43s	remaining: 675ms
2668:	learn: 0.0149752	total: 5.43s	remaining: 673ms
2669:	learn: 0.0149681	total: 5.43s	remaining: 671ms
2670:	learn: 0.0149641	total: 5.43s	remaining: 670ms
2671:	learn: 0.0149583	total: 5.44s	remaining: 668ms
2672:	learn: 0.0149546	total: 5.44s	remaining: 666ms
2673:	learn: 0.0149484	total: 5.44s	remaining: 664ms
2674:	learn: 0.0149444	total: 5.45s	remaining: 662ms
2675:	learn: 0.0149371	total: 5.45s	remaining: 660ms
2676:	learn: 0.0149304	total: 5.45s	remaining: 658ms
2677:	learn: 0.0149257	total: 5.45s	remaining: 656ms
2678:	learn: 0.0149202	total: 5.46s	remaining: 654ms
2679:	learn: 0.0149154	total: 5.46s	remaining: 652ms
2680:	learn: 0.0149091	total: 5.46s	remaining: 650ms
2681:	learn: 0.0149044	total: 5.46s	remaining: 648ms
2682:	learn: 0.0148978	total: 5.47s	remaining: 646ms
2683:	learn: 0.0148926	total: 5.47s	remaining: 644ms
2684:	learn: 0.0148864	total: 5.47s	remaining:

2846:	learn: 0.0140754	total: 5.8s	remaining: 312ms
2847:	learn: 0.0140691	total: 5.8s	remaining: 310ms
2848:	learn: 0.0140603	total: 5.8s	remaining: 308ms
2849:	learn: 0.0140563	total: 5.81s	remaining: 306ms
2850:	learn: 0.0140538	total: 5.81s	remaining: 304ms
2851:	learn: 0.0140520	total: 5.81s	remaining: 302ms
2852:	learn: 0.0140491	total: 5.81s	remaining: 300ms
2853:	learn: 0.0140436	total: 5.82s	remaining: 298ms
2854:	learn: 0.0140393	total: 5.82s	remaining: 296ms
2855:	learn: 0.0140333	total: 5.82s	remaining: 294ms
2856:	learn: 0.0140292	total: 5.83s	remaining: 292ms
2857:	learn: 0.0140242	total: 5.83s	remaining: 290ms
2858:	learn: 0.0140239	total: 5.83s	remaining: 288ms
2859:	learn: 0.0140215	total: 5.83s	remaining: 286ms
2860:	learn: 0.0140174	total: 5.84s	remaining: 284ms
2861:	learn: 0.0140122	total: 5.84s	remaining: 282ms
2862:	learn: 0.0140083	total: 5.84s	remaining: 280ms
2863:	learn: 0.0140038	total: 5.85s	remaining: 278ms
2864:	learn: 0.0140016	total: 5.85s	remaining: 27

In [21]:
stack2.fit(X,yt)
prediction=stack2.predict(test)
prediction=((prediction*lmda)+1)**(1/lmda)
pred = pd.DataFrame(prediction, columns=['SalePrice'])
ID = test_raw[['Id']]
sub=pd.merge(ID, pred, left_on = ID.index, right_on = pred.index).drop(columns=['key_0'])
sub.to_csv('../Submissions/stacked2.csv',index=False)
prediction

Learning rate set to 0.017396
0:	learn: 0.1505543	total: 4.68ms	remaining: 14s
1:	learn: 0.1487864	total: 7.19ms	remaining: 10.8s
2:	learn: 0.1471340	total: 9.67ms	remaining: 9.66s
3:	learn: 0.1454217	total: 11.8ms	remaining: 8.81s
4:	learn: 0.1438943	total: 14.2ms	remaining: 8.51s
5:	learn: 0.1422813	total: 16.7ms	remaining: 8.32s
6:	learn: 0.1408089	total: 19.3ms	remaining: 8.24s
7:	learn: 0.1392242	total: 21.3ms	remaining: 7.98s
8:	learn: 0.1377242	total: 23.6ms	remaining: 7.83s
9:	learn: 0.1363748	total: 25.6ms	remaining: 7.66s
10:	learn: 0.1348971	total: 27.6ms	remaining: 7.5s
11:	learn: 0.1334662	total: 29.6ms	remaining: 7.37s
12:	learn: 0.1322014	total: 31.5ms	remaining: 7.25s
13:	learn: 0.1307917	total: 33.5ms	remaining: 7.15s
14:	learn: 0.1294696	total: 35.9ms	remaining: 7.14s
15:	learn: 0.1280315	total: 38ms	remaining: 7.09s
16:	learn: 0.1267869	total: 40.2ms	remaining: 7.05s
17:	learn: 0.1254464	total: 42.2ms	remaining: 6.99s
18:	learn: 0.1241810	total: 44.2ms	remaining: 6.9

168:	learn: 0.0518271	total: 374ms	remaining: 6.27s
169:	learn: 0.0517124	total: 377ms	remaining: 6.27s
170:	learn: 0.0515781	total: 379ms	remaining: 6.27s
171:	learn: 0.0514577	total: 382ms	remaining: 6.27s
172:	learn: 0.0513503	total: 384ms	remaining: 6.27s
173:	learn: 0.0512196	total: 386ms	remaining: 6.28s
174:	learn: 0.0510948	total: 389ms	remaining: 6.28s
175:	learn: 0.0509453	total: 391ms	remaining: 6.28s
176:	learn: 0.0508216	total: 394ms	remaining: 6.28s
177:	learn: 0.0506650	total: 396ms	remaining: 6.28s
178:	learn: 0.0505400	total: 398ms	remaining: 6.28s
179:	learn: 0.0504164	total: 401ms	remaining: 6.28s
180:	learn: 0.0503046	total: 403ms	remaining: 6.28s
181:	learn: 0.0501722	total: 405ms	remaining: 6.28s
182:	learn: 0.0500616	total: 408ms	remaining: 6.29s
183:	learn: 0.0499315	total: 411ms	remaining: 6.29s
184:	learn: 0.0498222	total: 414ms	remaining: 6.29s
185:	learn: 0.0497034	total: 416ms	remaining: 6.29s
186:	learn: 0.0495909	total: 418ms	remaining: 6.29s
187:	learn: 

354:	learn: 0.0395818	total: 749ms	remaining: 5.58s
355:	learn: 0.0395477	total: 752ms	remaining: 5.58s
356:	learn: 0.0395173	total: 753ms	remaining: 5.57s
357:	learn: 0.0394891	total: 755ms	remaining: 5.57s
358:	learn: 0.0394452	total: 758ms	remaining: 5.57s
359:	learn: 0.0394227	total: 760ms	remaining: 5.57s
360:	learn: 0.0393820	total: 763ms	remaining: 5.57s
361:	learn: 0.0393585	total: 765ms	remaining: 5.57s
362:	learn: 0.0393250	total: 767ms	remaining: 5.57s
363:	learn: 0.0392958	total: 770ms	remaining: 5.57s
364:	learn: 0.0392560	total: 772ms	remaining: 5.57s
365:	learn: 0.0392239	total: 774ms	remaining: 5.57s
366:	learn: 0.0391980	total: 776ms	remaining: 5.57s
367:	learn: 0.0391623	total: 779ms	remaining: 5.57s
368:	learn: 0.0391397	total: 781ms	remaining: 5.57s
369:	learn: 0.0391111	total: 782ms	remaining: 5.56s
370:	learn: 0.0390679	total: 784ms	remaining: 5.55s
371:	learn: 0.0390380	total: 785ms	remaining: 5.55s
372:	learn: 0.0390003	total: 787ms	remaining: 5.54s
373:	learn: 

553:	learn: 0.0347107	total: 1.12s	remaining: 4.97s
554:	learn: 0.0347035	total: 1.13s	remaining: 4.97s
555:	learn: 0.0346784	total: 1.13s	remaining: 4.97s
556:	learn: 0.0346702	total: 1.13s	remaining: 4.97s
557:	learn: 0.0346677	total: 1.14s	remaining: 4.97s
558:	learn: 0.0346570	total: 1.14s	remaining: 4.97s
559:	learn: 0.0346500	total: 1.14s	remaining: 4.97s
560:	learn: 0.0346232	total: 1.14s	remaining: 4.97s
561:	learn: 0.0345921	total: 1.14s	remaining: 4.96s
562:	learn: 0.0345834	total: 1.15s	remaining: 4.96s
563:	learn: 0.0345527	total: 1.15s	remaining: 4.96s
564:	learn: 0.0345271	total: 1.15s	remaining: 4.96s
565:	learn: 0.0345220	total: 1.15s	remaining: 4.96s
566:	learn: 0.0344951	total: 1.15s	remaining: 4.95s
567:	learn: 0.0344787	total: 1.16s	remaining: 4.95s
568:	learn: 0.0344631	total: 1.16s	remaining: 4.94s
569:	learn: 0.0344358	total: 1.16s	remaining: 4.94s
570:	learn: 0.0344276	total: 1.16s	remaining: 4.94s
571:	learn: 0.0344121	total: 1.16s	remaining: 4.93s
572:	learn: 

785:	learn: 0.0307984	total: 1.5s	remaining: 4.22s
786:	learn: 0.0307834	total: 1.5s	remaining: 4.22s
787:	learn: 0.0307725	total: 1.5s	remaining: 4.22s
788:	learn: 0.0307685	total: 1.5s	remaining: 4.22s
789:	learn: 0.0307658	total: 1.51s	remaining: 4.22s
790:	learn: 0.0307636	total: 1.51s	remaining: 4.22s
791:	learn: 0.0307421	total: 1.51s	remaining: 4.22s
792:	learn: 0.0307345	total: 1.52s	remaining: 4.22s
793:	learn: 0.0307211	total: 1.52s	remaining: 4.22s
794:	learn: 0.0306970	total: 1.52s	remaining: 4.22s
795:	learn: 0.0306816	total: 1.52s	remaining: 4.22s
796:	learn: 0.0306591	total: 1.52s	remaining: 4.21s
797:	learn: 0.0306470	total: 1.53s	remaining: 4.21s
798:	learn: 0.0306277	total: 1.53s	remaining: 4.21s
799:	learn: 0.0306134	total: 1.53s	remaining: 4.21s
800:	learn: 0.0306023	total: 1.53s	remaining: 4.2s
801:	learn: 0.0305880	total: 1.53s	remaining: 4.2s
802:	learn: 0.0305852	total: 1.53s	remaining: 4.2s
803:	learn: 0.0305708	total: 1.54s	remaining: 4.2s
804:	learn: 0.030555

...

2418:	learn: 0.0184060	total: 5.24s	remaining: 1.26s
2419:	learn: 0.0184028	total: 5.24s	remaining: 1.26s
2420:	learn: 0.0183977	total: 5.25s	remaining: 1.25s
2421:	learn: 0.0183894	total: 5.25s	remaining: 1.25s
2422:	learn: 0.0183837	total: 5.25s	remaining: 1.25s
2423:	learn: 0.0183813	total: 5.25s	remaining: 1.25s
2424:	learn: 0.0183733	total: 5.26s	remaining: 1.25s
2425:	learn: 0.0183695	total: 5.26s	remaining: 1.24s
2426:	learn: 0.0183617	total: 5.26s	remaining: 1.24s
2427:	learn: 0.0183552	total: 5.26s	remaining: 1.24s
2428:	learn: 0.0183515	total: 5.27s	remaining: 1.24s
2429:	learn: 0.0183451	total: 5.27s	remaining: 1.24s
2430:	learn: 0.0183414	total: 5.27s	remaining: 1.23s
2431:	learn: 0.0183380	total: 5.27s	remaining: 1.23s
2432:	learn: 0.0183327	total: 5.28s	remaining: 1.23s
2433:	learn: 0.0183304	total: 5.28s	remaining: 1.23s
2434:	learn: 0.0183272	total: 5.28s	remaining: 1.23s
2435:	learn: 0.0183177	total: 5.29s	remaining: 1.22s
2436:	learn: 0.0183115	total: 5.29s	remaining:

2595:	learn: 0.0175203	total: 5.62s	remaining: 874ms
2596:	learn: 0.0175162	total: 5.62s	remaining: 872ms
2597:	learn: 0.0175098	total: 5.62s	remaining: 870ms
2598:	learn: 0.0175052	total: 5.62s	remaining: 868ms
2599:	learn: 0.0175017	total: 5.63s	remaining: 866ms
2600:	learn: 0.0174962	total: 5.63s	remaining: 864ms
2601:	learn: 0.0174912	total: 5.63s	remaining: 862ms
2602:	learn: 0.0174888	total: 5.63s	remaining: 860ms
2603:	learn: 0.0174848	total: 5.64s	remaining: 857ms
2604:	learn: 0.0174784	total: 5.64s	remaining: 856ms
2605:	learn: 0.0174721	total: 5.64s	remaining: 853ms
2606:	learn: 0.0174658	total: 5.65s	remaining: 851ms
2607:	learn: 0.0174571	total: 5.65s	remaining: 849ms
2608:	learn: 0.0174516	total: 5.65s	remaining: 847ms
2609:	learn: 0.0174482	total: 5.65s	remaining: 845ms
2610:	learn: 0.0174478	total: 5.66s	remaining: 843ms
2611:	learn: 0.0174415	total: 5.66s	remaining: 841ms
2612:	learn: 0.0174387	total: 5.66s	remaining: 838ms
2613:	learn: 0.0174332	total: 5.66s	remaining:

2765:	learn: 0.0167036	total: 5.99s	remaining: 507ms
2766:	learn: 0.0166981	total: 6s	remaining: 505ms
2767:	learn: 0.0166961	total: 6s	remaining: 503ms
2768:	learn: 0.0166890	total: 6s	remaining: 501ms
2769:	learn: 0.0166825	total: 6.01s	remaining: 499ms
2770:	learn: 0.0166806	total: 6.01s	remaining: 497ms
2771:	learn: 0.0166750	total: 6.01s	remaining: 495ms
2772:	learn: 0.0166722	total: 6.02s	remaining: 493ms
2773:	learn: 0.0166689	total: 6.02s	remaining: 490ms
2774:	learn: 0.0166654	total: 6.02s	remaining: 488ms
2775:	learn: 0.0166581	total: 6.03s	remaining: 486ms
2776:	learn: 0.0166534	total: 6.03s	remaining: 484ms
2777:	learn: 0.0166484	total: 6.03s	remaining: 482ms
2778:	learn: 0.0166434	total: 6.04s	remaining: 480ms
2779:	learn: 0.0166362	total: 6.04s	remaining: 478ms
2780:	learn: 0.0166336	total: 6.04s	remaining: 476ms
2781:	learn: 0.0166282	total: 6.04s	remaining: 474ms
2782:	learn: 0.0166248	total: 6.04s	remaining: 471ms
2783:	learn: 0.0166208	total: 6.05s	remaining: 469ms
27

2972:	learn: 0.0157748	total: 6.57s	remaining: 59.6ms
2973:	learn: 0.0157706	total: 6.57s	remaining: 57.4ms
2974:	learn: 0.0157631	total: 6.57s	remaining: 55.2ms
2975:	learn: 0.0157607	total: 6.57s	remaining: 53ms
2976:	learn: 0.0157538	total: 6.58s	remaining: 50.8ms
2977:	learn: 0.0157493	total: 6.58s	remaining: 48.6ms
2978:	learn: 0.0157471	total: 6.58s	remaining: 46.4ms
2979:	learn: 0.0157441	total: 6.59s	remaining: 44.2ms
2980:	learn: 0.0157396	total: 6.59s	remaining: 42ms
2981:	learn: 0.0157355	total: 6.59s	remaining: 39.8ms
2982:	learn: 0.0157314	total: 6.6s	remaining: 37.6ms
2983:	learn: 0.0157276	total: 6.6s	remaining: 35.4ms
2984:	learn: 0.0157207	total: 6.6s	remaining: 33.2ms
2985:	learn: 0.0157142	total: 6.61s	remaining: 31ms
2986:	learn: 0.0157107	total: 6.61s	remaining: 28.8ms
2987:	learn: 0.0157027	total: 6.61s	remaining: 26.6ms
2988:	learn: 0.0157005	total: 6.62s	remaining: 24.3ms
2989:	learn: 0.0156950	total: 6.62s	remaining: 22.1ms
2990:	learn: 0.0156904	total: 6.62s	r

array([122873.39914564, 160459.33900611, 183938.83070053, ...,
       165233.10940487, 123548.34962056, 220945.48286761])

## Top Performance in Kaggle

In [55]:
best_prediction = pd.read_csv('../Submissions/stacked2.csv')

In [57]:
# Estimated Total Value of the Portfolio of 1459 homes.
np.sum(best_prediction.SalePrice)

261036948.5809005